# Notebook for CME Futures Challenge

### The Rough Idea

Model indices as geometric brownian motion (dS/S = mudt + sigmadB)  
Model mu (market line) as a linear regression with numerous factors including economic, credit measures, etc  
Model sigma as a function of volatility including recent volatility and EMA (decay)  
Long/short based on futures mispricings based on our model  

# Downloading historical data for indices (S&P, NASDAQ, DJIA)

Imports

In [139]:
import yfinance as yf
import pandas as pd
import plotly.express as px
from typing import List, Dict

Make get_data function for downloading from yf

In [140]:
timeframe = '1000mo' # set timeframe

def get_data(tickers: List):
    data_dictionary = {}
    for ticker in tickers:
        data_dictionary[ticker] = yf.download(ticker, period=timeframe, interval='1d')
    return data_dictionary

Now let's get data for indices and display with pd

In [141]:
indices = ['^GSPC', '^IXIC', '^DJI'] # S&P, NASDAQ, DJIA
etfs = ['SPY', 'QQQ', 'DIA']
data_dictionary = get_data(etfs)

#s_p = pd.DataFrame(data_dictionary['^GSPC'])
#nasdaq = pd.DataFrame(data_dictionary['^IXIC'])
#djia = pd.DataFrame(data_dictionary['^DJI'])

s_p = pd.DataFrame(data_dictionary['SPY'])
nasdaq = pd.DataFrame(data_dictionary['QQQ'])
djia = pd.DataFrame(data_dictionary['DIA'])

C:\Users\rjsyo\AppData\Local\Temp\ipykernel_28800\3981970906.py:6: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  1 of 1 completed
C:\Users\rjsyo\AppData\Local\Temp\ipykernel_28800\3981970906.py:6: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  1 of 1 completed
C:\Users\rjsyo\AppData\Local\Temp\ipykernel_28800\3981970906.py:6: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  1 of 1 completed


In [142]:
s_p

Price            Close        High         Low        Open     Volume
Ticker             SPY         SPY         SPY         SPY        SPY
Date                                                                 
1993-01-29   24.313040   24.330332   24.209286   24.330332    1003200
1993-02-01   24.485958   24.485958   24.330327   24.330327     480500
1993-02-02   24.537838   24.555130   24.416792   24.468669     201300
1993-02-03   24.797226   24.814518   24.555133   24.572425     529400
1993-02-04   24.900970   24.952847   24.607001   24.883678     531500
...                ...         ...         ...         ...        ...
2025-09-15  659.082703  659.212348  657.517097  657.816255   63772400
2025-09-16  658.175232  659.950340  657.387438  659.641138   61169000
2025-09-17  657.357544  659.890500  652.491031  658.185266  101952200
2025-09-18  660.429016  663.051750  658.444528  660.060044   90459200
2025-09-19  663.700012  664.549988  660.369995  662.330017   97853200

[8217 rows x 5 columns]

We need to flatten this - notice ticker header

In [143]:
s_p = s_p.droplevel(1, axis=1)
nasdaq = nasdaq.droplevel(1, axis=1)
djia = djia.droplevel(1, axis=1)

In [144]:
s_p

Price            Close        High         Low        Open     Volume
Date                                                                 
1993-01-29   24.313040   24.330332   24.209286   24.330332    1003200
1993-02-01   24.485958   24.485958   24.330327   24.330327     480500
1993-02-02   24.537838   24.555130   24.416792   24.468669     201300
1993-02-03   24.797226   24.814518   24.555133   24.572425     529400
1993-02-04   24.900970   24.952847   24.607001   24.883678     531500
...                ...         ...         ...         ...        ...
2025-09-15  659.082703  659.212348  657.517097  657.816255   63772400
2025-09-16  658.175232  659.950340  657.387438  659.641138   61169000
2025-09-17  657.357544  659.890500  652.491031  658.185266  101952200
2025-09-18  660.429016  663.051750  658.444528  660.060044   90459200
2025-09-19  663.700012  664.549988  660.369995  662.330017   97853200

[8217 rows x 5 columns]

Let's drop high, low, and open and rename columns

In [145]:
s_p.drop(columns=['High', 'Low', 'Open'], inplace=True)
nasdaq.drop(columns=['High', 'Low', 'Open'], inplace=True)
djia.drop(columns=['High', 'Low', 'Open'], inplace=True)

s_p = s_p.rename(columns={'Close': 'S&P_Close', 'Volume': 'S&P_Volume'})
nasdaq = nasdaq.rename(columns={'Close': 'NASDAQ_Close', 'Volume': 'NASDAQ_Volume'})
djia = djia.rename(columns={'Close': 'DJIA_Close', 'Volume': 'DJIA_Volume'})

Let's get a quick plot of an index

In [146]:
fig = px.line(s_p, x=s_p.index, y="S&P_Close", title="S&P Daily Past 30 Years")
fig.show()

# Downloading historical data for our factor model

We are going to model the index as a geometric brownian motion, with the mu factor being a linear regression model with numerous inputs.  

## Factor considerations:  
### <u>Term structure</u>
###### Term spread (10Y-3M)

### <u>Credit conditions</u>
###### IG spread (BAA-AAA)

### <u>Valuation</u>
###### Forward E/P - real 10Y
###### Dividend yield

### <u>Economic</u>
###### Fed funds
###### Inflation (CPI)
###### DXY change (dollar index)  

### Some of these we can get from yahoo finance:  

In [147]:
tickers = [
    # Term structure
    '^TNX', # 10yr CBOE
    '^IRX', # 3m bill (on discount basis, need to convert to yield)

    # Economic
    'DX-Y.NYB', # Dollar index
]

data_dictionary = get_data(tickers)

ten_yr = pd.DataFrame(data_dictionary['^TNX']['Close'])
three_m = pd.DataFrame(data_dictionary['^IRX']['Close'])
dollar_index = pd.DataFrame(data_dictionary['DX-Y.NYB']['Close'])

C:\Users\rjsyo\AppData\Local\Temp\ipykernel_28800\3981970906.py:6: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  1 of 1 completed
C:\Users\rjsyo\AppData\Local\Temp\ipykernel_28800\3981970906.py:6: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  1 of 1 completed
C:\Users\rjsyo\AppData\Local\Temp\ipykernel_28800\3981970906.py:6: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  1 of 1 completed


Rename columns

In [148]:
ten_yr = ten_yr.rename(columns={'^TNX': 'ten_yr'})
three_m = three_m.rename(columns={'^IRX': 'three_m'})
dollar_index = dollar_index.rename(columns={'DX-Y.NYB': 'dollar_index'})

We should get dividend yield too

In [149]:
etfs = ['SPY', 'QQQ', 'DIA']
div_data = {}

for etf in etfs:
    ticker = yf.Ticker(etf)
    div = ticker.dividends
    price = ticker.history(timeframe)['Close']

    # Calculate dividend yield
    div_12m = div.rolling(window='365D', min_periods=1).sum()
    div_12m = div_12m.reindex(price.index, method='ffill')
    div_yield = div_12m / price
    div_data[etf] = div_yield

Fix index for all 3 and rename columns

In [150]:
div_data['SPY'].index = pd.to_datetime(div_data['SPY'].index).normalize().tz_localize(None) # Normalize puts date in format we want
div_data['QQQ'].index = pd.to_datetime(div_data['QQQ'].index).normalize().tz_localize(None) # Localize (none) makes sure it doesn't add our timezone
div_data['DIA'].index = pd.to_datetime(div_data['DIA'].index).normalize().tz_localize(None)

div_data['SPY'].name = 'SPY_div'
div_data['QQQ'].name = 'QQQ_div'
div_data['DIA'].name = 'DIA_div'

In [151]:
div_data['SPY']

Date
1993-01-29         NaN
1993-02-01         NaN
1993-02-02         NaN
1993-02-03         NaN
1993-02-04         NaN
                ...   
2025-09-15    0.013546
2025-09-16    0.013565
2025-09-17    0.013582
2025-09-18    0.013518
2025-09-19    0.013560
Name: SPY_div, Length: 8217, dtype: float64

### pandas_datareader lets us download fred data

In [152]:
from pandas_datareader import data as pdr
from datetime import datetime

In [153]:
start = datetime(1990,1,1) # Start date for download

# Macroeconomic data
gdp = pdr.DataReader("GDP", "fred", start)
cpi = pdr.DataReader("CPIAUCSL", "fred", start)
fedfunds = pdr.DataReader("FEDFUNDS", "fred", start)

# For some reason this download doesn't have the most recent fed funds rate
fedfunds = pd.concat([fedfunds['FEDFUNDS'], pd.Series([4.08], index=[datetime(2025,9,17)])])

# Credit risk data
ig_spread = pdr.DataReader("BAMLC0A4CBBB", "fred", start)   # BofA BBB corp minus Treasuries
#hy_spread = pdr.DataReader("BAMLH0A0HYM2", "fred", start)   # BofA US High Yield spread
#baa_spread = pdr.DataReader("BAA10Y", "fred", start)        # Moody’s Baa – 10Y Treasury

Rename series

In [154]:
cpi.name = 'CPI'
fedfunds.name = 'fed_funds'
ig_spread.name = 'credit_spread'

In [155]:
fred_data = [gdp, cpi, fedfunds, ig_spread]

# Last business day <= today
last_bday = pd.bdate_range(end=pd.Timestamp.today().normalize().tz_localize(None), periods=1)[0]

for i, df in enumerate(fred_data):
    s = df.squeeze() # make it a Series
    # Build a business-day index from the series start to last_bday
    bidx = pd.bdate_range(start=s.index.min(), end=last_bday)
    # Reindex to business days and forward-fill
    s = s.reindex(bidx, method='ffill')
    # Write back as a 1-col DataFrame with a proper name
    name = s.name if s.name else f"series_{i}"
    fred_data[i] = s.to_frame(name)

In [156]:
fred_data[0]

GDP
1990-01-01   5872.701
1990-01-02   5872.701
1990-01-03   5872.701
1990-01-04   5872.701
1990-01-05   5872.701
...               ...
2025-09-15  30353.902
2025-09-16  30353.902
2025-09-17  30353.902
2025-09-18  30353.902
2025-09-19  30353.902

[9320 rows x 1 columns]

Let's build a master dataframe

In [157]:
data = s_p.join([nasdaq, djia, div_data['SPY'], div_data['QQQ'], div_data['DIA'], ten_yr, three_m, dollar_index, fred_data[0], fred_data[1], fred_data[2], fred_data[3]])
data

S&P_Close   S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                           
1993-01-29   24.313040    1003200.0           NaN            NaN         NaN   
1993-02-01   24.485958     480500.0           NaN            NaN         NaN   
1993-02-02   24.537838     201300.0           NaN            NaN         NaN   
1993-02-03   24.797226     529400.0           NaN            NaN         NaN   
1993-02-04   24.900970     531500.0           NaN            NaN         NaN   
...                ...          ...           ...            ...         ...   
2025-09-15  659.082703   63772400.0    591.679993     44360300.0  458.759308   
2025-09-16  658.175232   61169000.0    591.179993     36942100.0  457.472961   
2025-09-17  657.357544  101952200.0    590.000000     69384800.0  459.945923   
2025-09-18  660.429016   90459200.0    595.320007     61069300.0  461.312012   
2025-09-19  663.700012   97853200.0    599.349976     58142500.0  462.940002   

            DJIA_Volume   SPY_div   QQQ_div   DIA_div  ten_yr  three_m  \
Date                                                                     
1993-01-29          NaN       NaN       NaN       NaN   6.390    2.900   
1993-02-01          NaN       NaN       NaN       NaN   6.380    2.900   
1993-02-02          NaN       NaN       NaN       NaN   6.460    2.960   
1993-02-03          NaN       NaN       NaN       NaN   6.450    2.930   
1993-02-04          NaN       NaN       NaN       NaN   6.390    2.900   
...                 ...       ...       ...       ...     ...      ...   
2025-09-15    4862200.0  0.013546  0.006052  0.015259   4.034    3.900   
2025-09-16    4526100.0  0.013565  0.006057  0.015301   4.026    3.890   
2025-09-17    5998000.0  0.013582  0.006069  0.015219   4.076    3.868   
2025-09-18    6681000.0  0.013518  0.006015  0.015174   4.104    3.880   
2025-09-19    5871400.0  0.013560  0.005975  0.017261   4.139    3.878   

            dollar_index        GDP  CPIAUCSL  fed_funds  BAMLC0A4CBBB  
Date                                                                    
1993-01-29     92.459999   6729.459   142.800       3.02           NaN  
1993-02-01     93.559998   6729.459   143.100       3.03           NaN  
1993-02-02     93.919998   6729.459   143.100       3.03           NaN  
1993-02-03     94.239998   6729.459   143.100       3.03           NaN  
1993-02-04     94.529999   6729.459   143.100       3.03           NaN  
...                  ...        ...       ...        ...           ...  
2025-09-15     97.300003  30353.902   323.364       4.33          0.95  
2025-09-16     96.629997  30353.902   323.364       4.33          0.96  
2025-09-17     96.870003  30353.902   323.364       4.08          0.96  
2025-09-18     97.349998  30353.902   323.364       4.08          0.94  
2025-09-19     97.647003  30353.902   323.364       4.08          0.94  

[8217 rows x 16 columns]

# Linear regression model

### Feature Engineering

We need to be careful to not include things such as raw moving averages that will leak volatility information into our drift prediction  

In [158]:
import numpy as np

Function definitions to help out

In [159]:
def rolling_mean(data, window):
    return data.rolling(window, min_periods=window).mean()

Features

#  (TODO: look at making features like diffs for economic metrics, figure out when economic metrics are released vs reported in data)

In [160]:
# First, make log prices / volumes of our data, then log normal assumptions are better and everything is additive
data['S&P_log_price'] = np.log(data['S&P_Close'])
data['NASDAQ_log_price'] = np.log(data['NASDAQ_Close'])
data['DJIA_log_price'] = np.log(data['DJIA_Close'])

data['S&P_log_volume'] = np.log(data['S&P_Volume'])
data['NASDAQ_log_volume'] = np.log(data['NASDAQ_Volume'])
data['DJIA_log_volume'] = np.log(data['DJIA_Volume'])

Setting our target returns metric

In [161]:
# Log returns (21 = 1 month)
days = 1
data['S&P_ret'] = data['S&P_log_price'].diff(days)
data['NASDAQ_ret'] = data['NASDAQ_log_price'].diff(days)
data['DJIA_ret'] = data['DJIA_log_price'].diff(days)

# Next month log returns -- This will be our target variable
data[['S&P_next_ret','NASDAQ_next_ret','DJIA_next_ret']] = data[['S&P_ret','NASDAQ_ret','DJIA_ret']].shift(-days).dropna()

ETF Features

In [162]:
# ===== S&P =====
# Price-based
data['S&P_mom_1w'] = data['S&P_log_price'].diff(5) # Total price change / momentum indicator
data['S&P_mom_3m'] = data['S&P_log_price'].diff(63)
data['S&P_3m_rolling_price'] = rolling_mean(data['S&P_log_price'], 63)
data['S&P_trend_speed_price'] = data['S&P_3m_rolling_price'].diff(5)  # How fast the 3m trend is changing on a weekly basis
data['S&P_trend_dist_price'] = data['S&P_log_price'] - data['S&P_3m_rolling_price']


# Volume-based (essentially the same as price for now)
data['S&P_vlm_1w'] = data['S&P_log_volume'].diff(5) # Total volume change / momentum indicator
data['S&P_vlm_1m'] = data['S&P_log_volume'].diff(21)
data['S&P_vlm_3m'] = data['S&P_log_volume'].diff(63)
data['S&P_3m_rolling_volume'] = rolling_mean(data['S&P_log_volume'], 63)
data['S&P_trend_speed_volume'] = data['S&P_3m_rolling_volume'].diff(5)  # How fast the 3m trend is changing on a weekly basis
data['S&P_trend_dist_volume'] = data['S&P_log_volume'] - data['S&P_3m_rolling_volume']

# ===== NASDAQ =====
# Price-based
data['NASDAQ_mom_1w'] = data['NASDAQ_log_price'].diff(5)  # Total price change / momentum indicator
data['NASDAQ_mom_3m'] = data['NASDAQ_log_price'].diff(63)
data['NASDAQ_3m_rolling_price'] = rolling_mean(data['NASDAQ_log_price'], 63)
data['NASDAQ_trend_speed_price'] = data['NASDAQ_3m_rolling_price'].diff(5)  # How fast the 3m trend is changing on a weekly basis
data['NASDAQ_trend_dist_price'] = data['NASDAQ_log_price'] - data['NASDAQ_3m_rolling_price']

# Volume-based (essentially the same as price for now)
data['NASDAQ_vlm_1w'] = data['NASDAQ_log_volume'].diff(5)  # Total volume change / momentum indicator
data['NASDAQ_vlm_1m'] = data['NASDAQ_log_volume'].diff(21)
data['NASDAQ_vlm_3m'] = data['NASDAQ_log_volume'].diff(63)
data['NASDAQ_3m_rolling_volume'] = rolling_mean(data['NASDAQ_log_volume'], 63)
data['NASDAQ_trend_speed_volume'] = data['NASDAQ_3m_rolling_volume'].diff(5)  # How fast the 3m trend is changing on a weekly basis
data['NASDAQ_trend_dist_volume'] = data['NASDAQ_log_volume'] - data['NASDAQ_3m_rolling_volume']

# ===== DJIA =====
# Price-based
data['DJIA_mom_1w'] = data['DJIA_log_price'].diff(5)  # Total price change / momentum indicator
data['DJIA_mom_3m'] = data['DJIA_log_price'].diff(63)
data['DJIA_3m_rolling_price'] = rolling_mean(data['DJIA_log_price'], 63)
data['DJIA_trend_speed_price'] = data['DJIA_3m_rolling_price'].diff(5)  # How fast the 3m trend is changing on a weekly basis
data['DJIA_trend_dist_price'] = data['DJIA_log_price'] - data['DJIA_3m_rolling_price']

# Volume-based (essentially the same as price for now)
data['DJIA_vlm_1w'] = data['DJIA_log_volume'].diff(5)  # Total volume change / momentum indicator
data['DJIA_vlm_1m'] = data['DJIA_log_volume'].diff(21)
data['DJIA_vlm_3m'] = data['DJIA_log_volume'].diff(63)
data['DJIA_3m_rolling_volume'] = rolling_mean(data['DJIA_log_volume'], 63)
data['DJIA_trend_speed_volume'] = data['DJIA_3m_rolling_volume'].diff(5)  # How fast the 3m trend is changing on a weekly basis
data['DJIA_trend_dist_volume'] = data['DJIA_log_volume'] - data['DJIA_3m_rolling_volume']

Macro features

Other features

In [163]:
month_dummies = pd.get_dummies(data.index.month, prefix="month")
month_dummies.set_index(data.index, inplace=True)
data = data.join(month_dummies)

In [164]:
data

S&P_Close   S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                           
1993-01-29   24.313040    1003200.0           NaN            NaN         NaN   
1993-02-01   24.485958     480500.0           NaN            NaN         NaN   
1993-02-02   24.537838     201300.0           NaN            NaN         NaN   
1993-02-03   24.797226     529400.0           NaN            NaN         NaN   
1993-02-04   24.900970     531500.0           NaN            NaN         NaN   
...                ...          ...           ...            ...         ...   
2025-09-15  659.082703   63772400.0    591.679993     44360300.0  458.759308   
2025-09-16  658.175232   61169000.0    591.179993     36942100.0  457.472961   
2025-09-17  657.357544  101952200.0    590.000000     69384800.0  459.945923   
2025-09-18  660.429016   90459200.0    595.320007     61069300.0  461.312012   
2025-09-19  663.700012   97853200.0    599.349976     58142500.0  462.940002   

            DJIA_Volume   SPY_div   QQQ_div   DIA_div  ten_yr  ...  month_3  \
Date                                                           ...            
1993-01-29          NaN       NaN       NaN       NaN   6.390  ...    False   
1993-02-01          NaN       NaN       NaN       NaN   6.380  ...    False   
1993-02-02          NaN       NaN       NaN       NaN   6.460  ...    False   
1993-02-03          NaN       NaN       NaN       NaN   6.450  ...    False   
1993-02-04          NaN       NaN       NaN       NaN   6.390  ...    False   
...                 ...       ...       ...       ...     ...  ...      ...   
2025-09-15    4862200.0  0.013546  0.006052  0.015259   4.034  ...    False   
2025-09-16    4526100.0  0.013565  0.006057  0.015301   4.026  ...    False   
2025-09-17    5998000.0  0.013582  0.006069  0.015219   4.076  ...    False   
2025-09-18    6681000.0  0.013518  0.006015  0.015174   4.104  ...    False   
2025-09-19    5871400.0  0.013560  0.005975  0.017261   4.139  ...    False   

            month_4  month_5  month_6  month_7  month_8  month_9  month_10  \
Date                                                                         
1993-01-29    False    False    False    False    False    False     False   
1993-02-01    False    False    False    False    False    False     False   
1993-02-02    False    False    False    False    False    False     False   
1993-02-03    False    False    False    False    False    False     False   
1993-02-04    False    False    False    False    False    False     False   
...             ...      ...      ...      ...      ...      ...       ...   
2025-09-15    False    False    False    False    False     True     False   
2025-09-16    False    False    False    False    False     True     False   
2025-09-17    False    False    False    False    False     True     False   
2025-09-18    False    False    False    False    False     True     False   
2025-09-19    False    False    False    False    False     True     False   

            month_11  month_12  
Date                            
1993-01-29     False     False  
1993-02-01     False     False  
1993-02-02     False     False  
1993-02-03     False     False  
1993-02-04     False     False  
...              ...       ...  
2025-09-15     False     False  
2025-09-16     False     False  
2025-09-17     False     False  
2025-09-18     False     False  
2025-09-19     False     False  

[8217 rows x 73 columns]

### Preprocessing Data

Let's check for NaNs

In [165]:
data.isna().sum()

S&P_Close           0
S&P_Volume          0
NASDAQ_Close     1542
NASDAQ_Volume    1542
DJIA_Close       1256
                 ... 
month_8             0
month_9             0
month_10            0
month_11            0
month_12            0
Length: 73, dtype: int64

Impute some NaNs with average

In [166]:
data['ten_yr'] = data['ten_yr'].fillna(data['ten_yr'].mean())
data['three_m'] = data['three_m'].fillna(data['three_m'].mean())
data['dollar_index'] = data['dollar_index'].fillna(data['dollar_index'].mean())
data['BAMLC0A4CBBB'] = data['BAMLC0A4CBBB'].fillna(data['BAMLC0A4CBBB'].mean())
#data['S&P_ret'] = data['S&P_ret'].fillna(data['S&P_ret'].mean())
#data['NASDAQ_ret'] = data['NASDAQ_ret'].fillna(data['NASDAQ_ret'].mean())
#data['DJIA_ret'] = data['DJIA_ret'].fillna(data['DJIA_ret'].mean())

Drop others

In [167]:
data = data.dropna()
data

S&P_Close   S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                           
2003-12-24   73.179497    8055800.0     30.408178     44840300.0   63.607738   
2003-12-26   73.232887    8308400.0     30.365829     25497600.0   63.650867   
2003-12-29   74.207565   22483700.0     30.865566     63296200.0   64.519936   
2003-12-30   74.220924   19559500.0     30.967216     48249400.0   64.304192   
2003-12-31   74.287666   31501800.0     30.882496     60494600.0   64.452141   
...                ...          ...           ...            ...         ...   
2025-09-12  655.592407   72780100.0    586.659973     50745900.0  458.011444   
2025-09-15  659.082703   63772400.0    591.679993     44360300.0  458.759308   
2025-09-16  658.175232   61169000.0    591.179993     36942100.0  457.472961   
2025-09-17  657.357544  101952200.0    590.000000     69384800.0  459.945923   
2025-09-18  660.429016   90459200.0    595.320007     61069300.0  461.312012   

            DJIA_Volume   SPY_div   QQQ_div   DIA_div  ten_yr  ...  month_3  \
Date                                                           ...            
2003-12-24    3742600.0  0.028232  0.000460  0.033565   4.187  ...    False   
2003-12-26    2088500.0  0.028211  0.000461  0.033542   4.148  ...    False   
2003-12-29    6589900.0  0.027841  0.000454  0.033091   4.230  ...    False   
2003-12-30    5478200.0  0.027836  0.000452  0.033202   4.279  ...    False   
2003-12-31    5658100.0  0.027811  0.000453  0.033125   4.257  ...    False   
...                 ...       ...       ...       ...     ...  ...      ...   
2025-09-12    3784600.0  0.013618  0.006104  0.015283   4.061  ...    False   
2025-09-15    4862200.0  0.013546  0.006052  0.015259   4.034  ...    False   
2025-09-16    4526100.0  0.013565  0.006057  0.015301   4.026  ...    False   
2025-09-17    5998000.0  0.013582  0.006069  0.015219   4.076  ...    False   
2025-09-18    6681000.0  0.013518  0.006015  0.015174   4.104  ...    False   

            month_4  month_5  month_6  month_7  month_8  month_9  month_10  \
Date                                                                         
2003-12-24    False    False    False    False    False    False     False   
2003-12-26    False    False    False    False    False    False     False   
2003-12-29    False    False    False    False    False    False     False   
2003-12-30    False    False    False    False    False    False     False   
2003-12-31    False    False    False    False    False    False     False   
...             ...      ...      ...      ...      ...      ...       ...   
2025-09-12    False    False    False    False    False     True     False   
2025-09-15    False    False    False    False    False     True     False   
2025-09-16    False    False    False    False    False     True     False   
2025-09-17    False    False    False    False    False     True     False   
2025-09-18    False    False    False    False    False     True     False   

            month_11  month_12  
Date                            
2003-12-24     False      True  
2003-12-26     False      True  
2003-12-29     False      True  
2003-12-30     False      True  
2003-12-31     False      True  
...              ...       ...  
2025-09-12     False     False  
2025-09-15     False     False  
2025-09-16     False     False  
2025-09-17     False     False  
2025-09-18     False     False  

[5468 rows x 73 columns]

### Split data

Training/testing 80/20 split

In [168]:
import math

In [169]:
cutoff = math.floor(len(data)*.8)
training_data = data.iloc[:cutoff]
testing_data = data.iloc[cutoff:]

In [170]:
display(training_data.tail(5))
display(testing_data.head(5))

S&P_Close   S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                           
2021-05-05  390.514465   60162200.0    320.486267     46219300.0  315.984802   
2021-05-06  393.632935   74321400.0    322.901825     46814300.0  318.966583   
2021-05-07  396.497742   67733800.0    325.522064     53324500.0  321.154602   
2021-05-10  392.571533   81852400.0    317.301208     60700500.0  321.025238   
2021-05-11  389.067871  116888000.0    316.862854     71963600.0  316.566315   

            DJIA_Volume   SPY_div   QQQ_div   DIA_div  ten_yr  ...  month_3  \
Date                                                           ...            
2021-05-05    3506100.0  0.017846  0.005439  0.018026   1.584  ...    False   
2021-05-06    4276700.0  0.017704  0.005398  0.017858   1.561  ...    False   
2021-05-07    3526500.0  0.017576  0.005354  0.017736   1.577  ...    False   
2021-05-10    6092500.0  0.017752  0.005493  0.017743   1.602  ...    False   
2021-05-11    8396400.0  0.017912  0.005501  0.017993   1.624  ...    False   

            month_4  month_5  month_6  month_7  month_8  month_9  month_10  \
Date                                                                         
2021-05-05    False     True    False    False    False    False     False   
2021-05-06    False     True    False    False    False    False     False   
2021-05-07    False     True    False    False    False    False     False   
2021-05-10    False     True    False    False    False    False     False   
2021-05-11    False     True    False    False    False    False     False   

            month_11  month_12  
Date                            
2021-05-05     False     False  
2021-05-06     False     False  
2021-05-07     False     False  
2021-05-10     False     False  
2021-05-11     False     False  

[5 rows x 73 columns]

S&P_Close   S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                           
2021-05-12  380.802063  134811000.0    308.661530     91164900.0  310.187134   
2021-05-13  385.376495  106394000.0    311.047852     69877800.0  314.295380   
2021-05-14  391.294037   82201600.0    317.914795     44370000.0  317.812622   
2021-05-17  390.298340   65129200.0    315.986115     39395000.0  317.249451   
2021-05-18  386.935669   59810200.0    313.853088     36528500.0  314.904694   

            DJIA_Volume   SPY_div   QQQ_div   DIA_div  ten_yr  ...  month_3  \
Date                                                           ...            
2021-05-12    7034100.0  0.018301  0.005647  0.018363   1.695  ...    False   
2021-05-13    5741300.0  0.018084  0.005604  0.018123   1.668  ...    False   
2021-05-14    4677300.0  0.017810  0.005483  0.017923   1.635  ...    False   
2021-05-17    3262200.0  0.017856  0.005516  0.017954   1.640  ...    False   
2021-05-18    3462300.0  0.018011  0.005554  0.018088   1.642  ...    False   

            month_4  month_5  month_6  month_7  month_8  month_9  month_10  \
Date                                                                         
2021-05-12    False     True    False    False    False    False     False   
2021-05-13    False     True    False    False    False    False     False   
2021-05-14    False     True    False    False    False    False     False   
2021-05-17    False     True    False    False    False    False     False   
2021-05-18    False     True    False    False    False    False     False   

            month_11  month_12  
Date                            
2021-05-12     False     False  
2021-05-13     False     False  
2021-05-14     False     False  
2021-05-17     False     False  
2021-05-18     False     False  

[5 rows x 73 columns]

### Normalize inputs

In [171]:
from sklearn.preprocessing import StandardScaler

In [172]:
# Make sure we only fit on training_data and explanatory variables
targets = ['S&P_next_ret', 'NASDAQ_next_ret', 'DJIA_next_ret']
dummies = [f'month_{month}' for month in range(1,13)]
columns_to_ignore = [] #['NASDAQ_next_ret', 'DJIA_next_ret']
columns_to_ignore.extend(dummies)
features = [column for column in training_data.columns if column not in targets and column not in columns_to_ignore]

scaler = StandardScaler()
scaler.fit(training_data[features]) # Fitting on training data

train_scaled = training_data.copy()
test_scaled = testing_data.copy()

train_scaled[features] = scaler.transform(training_data[features])
test_scaled[features] = scaler.transform(testing_data[features])

# Save info on standardization for later
variables_mu = pd.Series(scaler.mean_, index=features)
variables_sd = pd.Series(scaler.scale_, index=features)

### Linear Regression

In [173]:
from sklearn.linear_model import LinearRegression, RidgeCV, LassoCV
from sklearn.model_selection import TimeSeriesSplit
from sklearn.metrics import r2_score, root_mean_squared_error

We are going to test with and without ridge (which will help reduce the impact of collinearity)

In [174]:
# Function to get print results from the models
def eval_and_report(y_true, y_pred, model_name):
    print(f"{model_name:18s} | R^2: {r2_score(y_true, y_pred):.4f} | RMSE: {root_mean_squared_error(y_true, y_pred):.6f}")

In [176]:
# Models
results = {}

for target in targets:
    print(f"\n=== Target: {target} ===")
    X_train = train_scaled[features].copy()
    y_train = train_scaled[target].copy()
    X_test = test_scaled[features].copy()
    y_test = test_scaled[target].copy()

    # 1. Ordinary Least Squares (OLS)
    ols = LinearRegression()
    ols.fit(X_train, y_train)
    yhat_ols = ols.predict(X_test)
    eval_and_report(y_test, yhat_ols, "OLS")

    # Print top coefficients
    ols_coef = pd.Series(ols.coef_, index=features).sort_values(key=np.abs, ascending=False)
    print("Top OLS coeffs:\n", ols_coef.head(10))

    # 2. Ridge with CV over alphas (time-series CV)
    tscv = TimeSeriesSplit(n_splits=5)
    alphas = np.logspace(-4, 3, 30)

    ridge = RidgeCV(alphas=alphas, cv=tscv, fit_intercept=True)
    ridge.fit(X_train, y_train)
    yhat_ridge = ridge.predict(X_test)
    eval_and_report(y_test, yhat_ridge, f"Ridge (alpha={ridge.alpha_:.4g})")

    # Print top coefficients
    ridge_coef = pd.Series(ridge.coef_, index=features).sort_values(key=np.abs, ascending=False)
    print("Top Ridge coeffs:\n", ridge_coef.head(10))

    # 3. Lasso with CV over alphas (time-series CV)
    tscv = TimeSeriesSplit(n_splits=5)
    alphas = np.logspace(-4, 3, 30)

    lasso = LassoCV(alphas=alphas, cv=tscv, fit_intercept=True)
    lasso.fit(X_train, y_train)
    yhat_lasso = lasso.predict(X_test)
    eval_and_report(y_test, yhat_lasso, f"Lasso (alpha={lasso.alpha_:.4g})")

    # Print top coefficients
    lasso_coef = pd.Series(lasso.coef_, index=features).sort_values(key=np.abs, ascending=False)
    print("Top Lasso coeffs:\n", lasso_coef.head(10))

    # Store for later use
    results[target] = {
        "ols_model": ols,
        "ridge_model": ridge,
        "ols_coefs": ols_coef,
        "ridge_coefs": ridge_coef,
        "lasso_coefs": lasso_coef,
        "train_data_ols": pd.Series(ols.predict(X_train), index=y_train.index, name=f"OLS_train"),
        "train_data_ridge": pd.Series(ridge.predict(X_train), index=y_train.index, name=f"Ridge_train"),
        "train_data_lasso": pd.Series(lasso.predict(X_train), index=y_train.index, name=f"Lasso_train"),
        "yhat_ols": pd.Series(yhat_ols, index=y_test.index, name=f"{target}_OLS_pred"),
        "yhat_ridge": pd.Series(yhat_ridge, index=y_test.index, name=f"{target}_Ridge_pred"),
        "yhat_lasso": pd.Series(yhat_lasso, index=y_test.index, name=f"{target}_Ridge_pred"),
    }


=== Target: S&P_next_ret ===
OLS                | R^2: -4.8000 | RMSE: 0.026608
Top OLS coeffs:
 S&P_Close                  0.054546
DJIA_Close                -0.043389
S&P_3m_rolling_price      -0.034082
S&P_log_price             -0.033880
DJIA_3m_rolling_price      0.020646
DJIA_log_price             0.020606
NASDAQ_Close              -0.011978
NASDAQ_3m_rolling_price    0.011178
NASDAQ_log_price           0.011082
S&P_mom_3m                -0.010442
dtype: float64
Ridge (alpha=1000) | R^2: 0.0006 | RMSE: 0.011045
Top Ridge coeffs:
 DJIA_ret        -0.000636
S&P_mom_1w      -0.000600
S&P_ret         -0.000583
DIA_div          0.000439
S&P_vlm_1m      -0.000366
ten_yr          -0.000357
NASDAQ_Volume   -0.000347
S&P_Volume      -0.000308
BAMLC0A4CBBB    -0.000288
S&P_vlm_1w       0.000238
dtype: float64
Lasso (alpha=0.0003039) | R^2: -0.0019 | RMSE: 0.011059
Top Lasso coeffs:
 DJIA_ret        -0.000920
S&P_mom_1w      -0.000222
NASDAQ_Volume   -0.000166
S&P_ret         -0.000135
NASD

Let's try OLS again with PCA

In [177]:
from sklearn.decomposition import PCA

In [178]:
pca = PCA(n_components=.95).fit(train_scaled) # keep 95% of variance and fit to training set
train_pca = pca.transform(train_scaled)
test_pca = pca.transform(test_scaled)

In [179]:
# PCA
for target in targets:
    print(f"\n=== Target: {target} ===")
    y_train = train_scaled[target].copy()
    y_test  = test_scaled[target].copy()

    # 1) OLS on PCA components
    ols_pca = LinearRegression()
    ols_pca.fit(train_pca, y_train)
    yhat_pca = ols_pca.predict(test_pca)
    eval_and_report(y_test, yhat_pca, "OLS+PCA")

    results[target].update({
        "pca_model": ols_pca,
        "train_data_pca": pd.Series(ols_pca.predict(train_pca), index=y_train.index, name=f"PCA_train"),
        "yhat_pca": pd.Series(yhat_pca, index=y_test.index, name=f"{target}_PCA_pred")
    })


=== Target: S&P_next_ret ===
OLS+PCA            | R^2: -0.0086 | RMSE: 0.011096

=== Target: NASDAQ_next_ret ===
OLS+PCA            | R^2: -0.0007 | RMSE: 0.014459

=== Target: DJIA_next_ret ===
OLS+PCA            | R^2: -0.0199 | RMSE: 0.009551


Plot these results

In [180]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

In [181]:
# Pairs: (pretty name, next-return target key)
pairs = [
    ("S&P 500", "S&P_next_ret"),
    ("NASDAQ",  "NASDAQ_next_ret"),
    ("DJIA",    "DJIA_next_ret"),
]

def get_pred(results_dict, target_key, kind):
    """
    kind: 'ols', 'ridge', or 'pca'
    Prefer unstandardized preds if present, otherwise fall back to raw.
    """
    unstd_key = f"yhat_{kind}_unstd"
    std_key   = f"yhat_{kind}"
    if target_key in results_dict:
        if unstd_key in results_dict[target_key]:
            return results_dict[target_key][unstd_key]
        elif std_key in results_dict[target_key]:
            return results_dict[target_key][std_key]
    return None

fig = make_subplots(
    rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.06,
    subplot_titles=[p[0] for p in pairs]
)

for i, (label, next_col) in enumerate(pairs, start=1):
    if next_col not in testing_data.columns:
        continue

    # True = next-period return from testing_data (unscaled)
    y_true = testing_data[next_col].dropna().sort_index().rename("True")

    # Predictions for the same target
    yhat_ols   = get_pred(results, next_col, "ols")
    yhat_ridge = get_pred(results, next_col, "ridge")
    yhat_pca   = get_pred(results, next_col, "pca")
    yhat_lasso = get_pred(results, next_col, "lasso")

    parts = [y_true]
    if yhat_ols is not None:
        parts.append(yhat_ols.rename("OLS").reindex(y_true.index))
    if yhat_ridge is not None:
        parts.append(yhat_ridge.rename("Ridge").reindex(y_true.index))
    if yhat_pca is not None:
        parts.append(yhat_pca.rename("PCA").reindex(y_true.index))
    if yhat_lasso is not None:
        parts.append(yhat_lasso.rename("Lasso").reindex(y_true.index))

    df = pd.concat(parts, axis=1).dropna(how="any")
    if df.empty:
        continue

    show_leg = (i == 1)

    # True next_ret
    fig.add_trace(
        go.Scatter(x=df.index, y=df["True"], name="True next_ret",
                   mode="lines", line=dict(width=1.6),
                   showlegend=show_leg, legendgroup="true"),
        row=i, col=1
    )
    """
    # OLS prediction
    if "OLS" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["OLS"], name="OLS prediction",
                       mode="lines", line=dict(width=1.4, dash="dash"),
                       showlegend=show_leg, legendgroup="ols"),
            row=i, col=1
        )
    """
    # Ridge prediction
    if "Ridge" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["Ridge"], name="Ridge prediction",
                       mode="lines", line=dict(width=1.4, dash="dot"),
                       showlegend=show_leg, legendgroup="ridge"),
            row=i, col=1
        )
    # PCA prediction
    if "PCA" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["PCA"], name="PCA prediction",
                       mode="lines", line=dict(width=1.4, dash="longdash"),
                       showlegend=show_leg, legendgroup="pca"),
            row=i, col=1
        )
    # Lasso prediction
    if "PCA" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["Lasso"], name="Lasso prediction",
                       mode="lines", line=dict(width=1.4, dash="dash"),
                       showlegend=show_leg, legendgroup="lasso"),
            row=i, col=1
        )

fig.update_layout(
    title="Testing: True Next-Period Log Returns vs OLS, Ridge & PCA Predictions",
    height=900,
    hovermode="x unified",
    template="plotly_white",
    margin=dict(t=80, r=30, b=80, l=70),
    legend=dict(orientation="h", yanchor="top", y=-0.12, xanchor="left", x=0)
)

for r in range(1, 4):
    fig.update_yaxes(title_text="Log return", row=r, col=1)

# Range tools on the bottom axis
fig.update_xaxes(
    rangeselector=dict(buttons=[
        dict(step="all", label="All"),
        dict(count=3, step="year", stepmode="backward", label="3Y"),
        dict(count=1, step="year", stepmode="backward", label="1Y"),
        dict(count=6, step="month", stepmode="backward", label="6M"),
        dict(count=1, step="month", stepmode="backward", label="1M"),
    ]),
    rangeslider=dict(visible=True),
    row=3, col=1
)

fig.show()


# It looks like this may be an ok base for mu. Let's try to build sigma.

In [182]:
vol_data = s_p.join([nasdaq, djia])
vol_data

Price        S&P_Close  S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                          
1993-01-29   24.313040     1003200           NaN            NaN         NaN   
1993-02-01   24.485958      480500           NaN            NaN         NaN   
1993-02-02   24.537838      201300           NaN            NaN         NaN   
1993-02-03   24.797226      529400           NaN            NaN         NaN   
1993-02-04   24.900970      531500           NaN            NaN         NaN   
...                ...         ...           ...            ...         ...   
2025-09-15  659.082703    63772400    591.679993     44360300.0  458.759308   
2025-09-16  658.175232    61169000    591.179993     36942100.0  457.472961   
2025-09-17  657.357544   101952200    590.000000     69384800.0  459.945923   
2025-09-18  660.429016    90459200    595.320007     61069300.0  461.312012   
2025-09-19  663.700012    97853200    599.349976     58142500.0  462.940002   

Price       DJIA_Volume  
Date                     
1993-01-29          NaN  
1993-02-01          NaN  
1993-02-02          NaN  
1993-02-03          NaN  
1993-02-04          NaN  
...                 ...  
2025-09-15    4862200.0  
2025-09-16    4526100.0  
2025-09-17    5998000.0  
2025-09-18    6681000.0  
2025-09-19    5871400.0  

[8217 rows x 6 columns]

In [183]:
# First, make log prices / volumes of our data, then log normal assumptions are better and everything is additive
vol_data['S&P_log_price'] = np.log(vol_data['S&P_Close'])
vol_data['NASDAQ_log_price'] = np.log(vol_data['NASDAQ_Close'])
vol_data['DJIA_log_price'] = np.log(vol_data['DJIA_Close'])

vol_data['S&P_log_volume'] = np.log(data['S&P_Volume'])
vol_data['NASDAQ_log_volume'] = np.log(data['NASDAQ_Volume'])
vol_data['DJIA_log_volume'] = np.log(data['DJIA_Volume'])

# Log returns
vol_data['S&P_ret'] = vol_data['S&P_log_price'].diff(days)
vol_data['NASDAQ_ret'] = vol_data['NASDAQ_log_price'].diff(days)
vol_data['DJIA_ret'] = vol_data['DJIA_log_price'].diff(days)

# Next month log returns
vol_data[['S&P_next_ret','NASDAQ_next_ret','DJIA_next_ret']] = vol_data[['S&P_ret','NASDAQ_ret','DJIA_ret']].shift(-days).dropna()

# Residuals from previous
vol_data['S&P_next_ret'] = vol_data['S&P_next_ret'] - pd.concat([results['S&P_next_ret']['train_data_pca'],results['S&P_next_ret']['yhat_pca']])
vol_data['NASDAQ_ret'] = vol_data['NASDAQ_ret'] - pd.concat([results['NASDAQ_next_ret']['train_data_pca'],results['NASDAQ_next_ret']['yhat_pca']])
vol_data['DJIA_ret'] = vol_data['DJIA_ret'] - pd.concat([results['DJIA_next_ret']['train_data_pca'],results['DJIA_next_ret']['yhat_pca']])


# TODO: Change this, ripped straight from GPT as a quick test

In [184]:
EPS = 1e-12

# If you already have a rolling_mean helper, keep it. Otherwise:
def rolling_mean(s, w):
    return s.rolling(w, min_periods=max(2, int(w*0.6))).mean()

def ewma_vol(r, lam=0.94):
    # EWMA variance per RiskMetrics: sigma_t^2 = (1-lam)*r_{t-1}^2 + lam*sigma_{t-1}^2
    # Use pandas ewm for convenience
    return r.pow(2).ewm(alpha=(1-lam), adjust=False).mean().clip(lower=0)

def rolling_autocorr(x, lag=1, window=63):
    # Rolling autocorrelation of x at a given lag
    # For stability, require at least ~60% of window
    minp = max(10, int(window*0.6))
    x0 = x
    x1 = x.shift(lag)
    return x0.rolling(window, min_periods=minp).corr(x1)

def realized_quarticity(r, window=63):
    # 3-month robust quarticity proxy (if daily): sum r^4 * (n / 3) approximation
    # Here we simply provide rolling sum of r^4; scaling optional depending on use
    minp = max(10, int(window*0.6))
    return (r.pow(4)).rolling(window, min_periods=minp).sum()

def build_vol_features(data, prefix, day_w=21, qtr_w=63, yr_w=252, ewma_lambda=0.94):
    """
    Expects:
      data[f'{prefix}_log_price'] (daily log price)
      data[f'{prefix}_log_volume'] (daily log volume)
    Produces a suite of volatility-centric features for that prefix.
    """
    lp = data[f"{prefix}_log_price"]
    lv = data.get(f"{prefix}_log_volume", None)

    # Daily log return
    r = lp.diff()  # already log-price, so diff = log-return

    # --- Realized volatility proxies ---
    data[f"{prefix}_rv_1m"]  = r.rolling(day_w, min_periods=int(day_w*0.6)).var().clip(lower=0)          # variance
    data[f"{prefix}_rv_3m"]  = r.rolling(qtr_w, min_periods=int(qtr_w*0.6)).var().clip(lower=0)
    data[f"{prefix}_rv_1y"]  = r.rolling(yr_w,  min_periods=int(yr_w*0.6)).var().clip(lower=0)
    data[f"{prefix}_absrv_1m"] = r.abs().rolling(day_w, min_periods=int(day_w*0.6)).mean()               # mean |r|
    data[f"{prefix}_absrv_3m"] = r.abs().rolling(qtr_w, min_periods=int(qtr_w*0.6)).mean()

    # EWMA volatility (RiskMetrics-style)
    data[f"{prefix}_ewma_var"] = ewma_vol(r, lam=ewma_lambda)
    data[f"{prefix}_ewma_vol"] = np.sqrt(data[f"{prefix}_ewma_var"])

    # Volatility-of-volatility (how fast vol is changing)
    data[f"{prefix}_vol_speed_1w"] = data[f"{prefix}_rv_3m"].diff(5)                                      # weekly change in 3m var
    data[f"{prefix}_vol_mom_1m"]   = data[f"{prefix}_rv_3m"] - data[f"{prefix}_rv_1m"]                    # 3m vs 1m
    data[f"{prefix}_vol_mom_1y"]   = data[f"{prefix}_rv_1y"] - data[f"{prefix}_rv_3m"]

    # Volatility clustering proxies
    data[f"{prefix}_acf_sqret_lag1_3m"] = rolling_autocorr(r.pow(2), lag=1, window=qtr_w)
    data[f"{prefix}_acf_absret_lag1_3m"] = rolling_autocorr(r.abs(), lag=1, window=qtr_w)

    # Leverage effect proxy (contemporaneous corr between return and next day's vol)
    # Negative returns often precede higher vol; we proxy with corr(r_t, |r|_{t+1})
    data[f"{prefix}_lev_proxy_3m"] = r.rolling(qtr_w, min_periods=int(qtr_w*0.6)).corr(r.abs().shift(-1))

    # Quarticity (heavy tails proxy)
    data[f"{prefix}_quarticity_3m"] = realized_quarticity(r, window=qtr_w)

    # Ratio features (normalized vol levels)
    data[f"{prefix}_vol_ratio_1m_3m"] = (data[f"{prefix}_rv_1m"] / (data[f"{prefix}_rv_3m"] + EPS))
    data[f"{prefix}_vol_ratio_3m_1y"] = (data[f"{prefix}_rv_3m"] / (data[f"{prefix}_rv_1y"] + EPS))
    data[f"{prefix}_ewma_over_3m"]    = (data[f"{prefix}_ewma_var"] / (data[f"{prefix}_rv_3m"] + EPS))

    # Price–volatility relation: distance from trend as a stress proxy
    data[f"{prefix}_price_trend_3m"]  = rolling_mean(lp, qtr_w)
    data[f"{prefix}_price_trend_dist"] = lp - data[f"{prefix}_price_trend_3m"]
    # Volatility when far below trend often spikes; include interaction
    data[f"{prefix}_vol_x_trend_dist"] = data[f"{prefix}_rv_1m"] * data[f"{prefix}_price_trend_dist"]

    # Volume–volatility links (if volume available)
    if lv is not None:
        dv = lv.diff()  # log-volume change
        data[f"{prefix}_vlm_var_1m"] = dv.rolling(day_w, min_periods=int(day_w*0.6)).var().clip(lower=0)
        data[f"{prefix}_vlm_var_3m"] = dv.rolling(qtr_w, min_periods=int(qtr_w*0.6)).var().clip(lower=0)
        # Corr between |r| and volume changes (vol–volume clustering)
        data[f"{prefix}_corr_absr_dlv_3m"] = r.abs().rolling(qtr_w, min_periods=int(qtr_w*0.6)).corr(dv)
        # Volume surprise proxy: current vs 3m trend
        data[f"{prefix}_vlm_trend_3m"] = rolling_mean(lv, qtr_w)
        data[f"{prefix}_vlm_trend_dist"] = lv - data[f"{prefix}_vlm_trend_3m"]
        # Vol reacts to volume surprises
        data[f"{prefix}_vol_x_vlm_surprise"] = data[f"{prefix}_rv_1m"] * data[f"{prefix}_vlm_trend_dist"]

    # Optional: implied vs realized vol spread if you have VIX-like series
    # if f"{prefix}_impl_vol" in data.columns:
    #     data[f"{prefix}_ivr_spread"] = data[f"{prefix}_impl_vol"]**2 - data[f"{prefix}_rv_1m"]

    # Forward-looking realized vol target example (if needed)
    # data[f"{prefix}_fwd_rv_1m"] = r.shift(-1).rolling(day_w, min_periods=int(day_w*0.6)).var()

    return data

# ---- Apply to all indices ----
IDX_PREFIXES = ["S&P", "NASDAQ", "DJIA"]
for pfx in IDX_PREFIXES:
    vol_data = build_vol_features(vol_data, pfx, day_w=21, qtr_w=63, yr_w=252, ewma_lambda=0.94)

# ---- Cross-index spillover features (optional but useful) ----
# Differences/spreads in contemporaneous vol across indices capture contagion/regime moves
vol_data["SPX_minus_NDX_vol_1m"] = vol_data["S&P_rv_1m"] - vol_data["NASDAQ_rv_1m"]
vol_data["SPX_minus_DJIA_vol_1m"] = vol_data["S&P_rv_1m"] - vol_data["DJIA_rv_1m"]
vol_data["NDX_minus_DJIA_vol_1m"] = vol_data["NASDAQ_rv_1m"] - vol_data["DJIA_rv_1m"]

# A simple global vol factor: first PC of 3m realized vars (if you want a single factor)
try:
    _X = vol_data[["S&P_rv_3m", "NASDAQ_rv_3m", "DJIA_rv_3m"]].dropna()
    _Xc = (_X - _X.mean()) / (_X.std(ddof=0) + EPS)
    # first PC (no scikit-learn to keep it lightweight)
    U, S, Vt = np.linalg.svd(_Xc.values, full_matrices=False)
    gvol = pd.Series(U[:, 0]*S[0], index=_X.index, name="global_vol_pc1")
    vol_data["global_vol_pc1"] = gvol.reindex(data.index)
except Exception:
    pass

vol_data.dropna(inplace=True)

In [185]:
vol_data

Price        S&P_Close  S&P_Volume  NASDAQ_Close  NASDAQ_Volume  DJIA_Close  \
Date                                                                          
2004-02-19   76.924591    51146200     31.322954    100843800.0   66.054482   
2004-02-20   76.690948    46728800     31.221321    132347600.0   65.799721   
2004-02-23   76.497383    36357000     30.874027    125199800.0   65.682289   
2004-02-24   76.363815    43953000     30.797806    124521900.0   65.435005   
2004-02-25   76.684303    31213600     30.984158     74457100.0   65.657585   
...                ...         ...           ...            ...         ...   
2025-09-12  655.592407    72780100    586.659973     50745900.0  458.011444   
2025-09-15  659.082703    63772400    591.679993     44360300.0  458.759308   
2025-09-16  658.175232    61169000    591.179993     36942100.0  457.472961   
2025-09-17  657.357544   101952200    590.000000     69384800.0  459.945923   
2025-09-18  660.429016    90459200    595.320007     61069300.0  461.312012   

Price       DJIA_Volume  S&P_log_price  NASDAQ_log_price  DJIA_log_price  \
Date                                                                       
2004-02-19    6430900.0       4.342826          3.444351        4.190480   
2004-02-20    9334700.0       4.339784          3.441101        4.186616   
2004-02-23    7350700.0       4.337257          3.429915        4.184829   
2004-02-24    7973900.0       4.335509          3.427443        4.181057   
2004-02-25    4212700.0       4.339697          3.433476        4.184453   
...                 ...            ...               ...             ...   
2025-09-12    3784600.0       6.485539          6.374445        6.126894   
2025-09-15    4862200.0       6.490849          6.382966        6.128526   
2025-09-16    4526100.0       6.489471          6.382121        6.125718   
2025-09-17    5998000.0       6.488228          6.380123        6.131109   
2025-09-18    6681000.0       6.492890          6.389099        6.134075   

Price       S&P_log_volume  ...  DJIA_vlm_var_1m  DJIA_vlm_var_3m  \
Date                        ...                                     
2004-02-19       17.750199  ...         0.183854         0.163275   
2004-02-20       17.659871  ...         0.190730         0.162235   
2004-02-23       17.408897  ...         0.184047         0.159739   
2004-02-24       17.598631  ...         0.183610         0.155746   
2004-02-25       17.256364  ...         0.203312         0.162379   
...                    ...  ...              ...              ...   
2025-09-12       18.102953  ...         0.144960         0.113274   
2025-09-15       17.970831  ...         0.143888         0.108058   
2025-09-16       17.929151  ...         0.141966         0.105289   
2025-09-17       18.440015  ...         0.138226         0.105306   
2025-09-18       18.320409  ...         0.130447         0.105236   

Price       DJIA_corr_absr_dlv_3m  DJIA_vlm_trend_3m  DJIA_vlm_trend_dist  \
Date                                                                        
2004-02-19               0.362757          15.637369             0.039256   
2004-02-20               0.352612          15.647930             0.401319   
2004-02-23               0.360865          15.651989             0.158317   
2004-02-24               0.359392          15.657835             0.233849   
2004-02-25               0.360923          15.648211            -0.394597   
...                           ...                ...                  ...   
2025-09-12               0.474106          15.188782            -0.042331   
2025-09-15               0.412614          15.188900             0.208102   
2025-09-16               0.434828          15.194517             0.130854   
2025-09-17               0.442951          15.208728             0.398209   
2025-09-18               0.450598          15.222607             0.492171   

Price       DJIA_vol_x_vlm_surprise  SPX_minus_NDX_vol_1m  \
Date                  

In [186]:
month_dummies = pd.get_dummies(vol_data.index.month, prefix="month")
month_dummies.set_index(vol_data.index, inplace=True)
vol_data = vol_data.join(month_dummies)

In [187]:

cutoff = math.floor(len(vol_data)*.8)
training_data = vol_data.iloc[:cutoff]
testing_data = vol_data.iloc[cutoff:]
# Make sure we only fit on training_data and explanatory variables
targets = ['S&P_next_ret', 'NASDAQ_next_ret', 'DJIA_next_ret']
dummies = [f'month_{month}' for month in range(1,13)]
features = [column for column in training_data.columns if column not in targets and column not in dummies]

scaler = StandardScaler()
scaler.fit(training_data[features]) # Fitting on training data

train_scaled = training_data.copy()
test_scaled = testing_data.copy()

train_scaled[features] = scaler.transform(training_data[features])
test_scaled[features] = scaler.transform(testing_data[features])

# Save info on standardization for later
variables_mu = pd.Series(scaler.mean_, index=features)
variables_sd = pd.Series(scaler.scale_, index=features)

In [189]:
# Models
results_sigma = {}

for target in targets:
    print(f"\n=== Target: {target} ===")
    X_train = train_scaled[features].copy()
    y_train = train_scaled[target].copy()
    X_test = test_scaled[features].copy()
    y_test = test_scaled[target].copy()

    # 1. Ordinary Least Squares (OLS)
    ols = LinearRegression()
    ols.fit(X_train, y_train)
    yhat_ols = ols.predict(X_test)
    eval_and_report(y_test, yhat_ols, "OLS")

    # Print top coefficients
    ols_coef = pd.Series(ols.coef_, index=features).sort_values(key=np.abs, ascending=False)
    print("Top OLS coeffs:\n", ols_coef.head(10))

    # 2. Ridge with CV over alphas (time-series CV)
    tscv = TimeSeriesSplit(n_splits=5)
    alphas = np.logspace(-4, 3, 30)

    ridge = RidgeCV(alphas=alphas, cv=tscv, fit_intercept=True)
    ridge.fit(X_train, y_train)
    yhat_ridge = ridge.predict(X_test)
    eval_and_report(y_test, yhat_ridge, f"Ridge: alpha={ridge.alpha_:.4g})")

    # Print top coefficients
    ridge_coef = pd.Series(ridge.coef_, index=features).sort_values(key=np.abs, ascending=False)
    print("Top Ridge coeffs:\n", ridge_coef.head(10))

    # 3. Lasso with CV over alphas (time-series CV)
    tscv = TimeSeriesSplit(n_splits=5)
    alphas = np.logspace(-4, 3, 30)

    lasso = LassoCV(alphas=alphas, cv=tscv, fit_intercept=True)
    lasso.fit(X_train, y_train)
    yhat_lasso = lasso.predict(X_test)
    eval_and_report(y_test, yhat_lasso, f"Lasso (alpha={lasso.alpha_:.4g})")

    # Print top coefficients
    lasso_coef = pd.Series(lasso.coef_, index=features).sort_values(key=np.abs, ascending=False)
    print("Top Lasso coeffs:\n", lasso_coef.head(10))

    # Store for later use
    results_sigma[target] = {
        "ols_model": ols,
        "ridge_model": ridge,
        "ols_coefs": ols_coef,
        "ridge_coefs": ridge_coef,
        "lasso_coefs": lasso_coef,
        "train_data_ols": pd.Series(ols.predict(X_train), index=y_train.index, name=f"OLS_train"),
        "train_data_ridge": pd.Series(ridge.predict(X_train), index=y_train.index, name=f"Ridge_train"),
        "train_data_lasso": pd.Series(lasso.predict(X_train), index=y_train.index, name=f"Lasso_train"),
        "yhat_ols": pd.Series(yhat_ols, index=y_test.index, name=f"{target}_OLS_pred"),
        "yhat_ridge": pd.Series(yhat_ridge, index=y_test.index, name=f"{target}_Ridge_pred"),
        "yhat_lasso": pd.Series(yhat_lasso, index=y_test.index, name=f"{target}_Ridge_pred"),
    }


=== Target: S&P_next_ret ===
OLS                | R^2: -4.5294 | RMSE: 0.026058
Top OLS coeffs:
 DJIA_quarticity_3m         0.033700
S&P_vol_x_trend_dist      -0.029455
S&P_ewma_vol              -0.029303
NASDAQ_quarticity_3m      -0.027754
DJIA_ewma_vol              0.027753
S&P_Close                 -0.025975
DJIA_Close                 0.025083
NASDAQ_vol_x_trend_dist    0.015279
S&P_absrv_1m               0.013533
S&P_price_trend_3m         0.013343
dtype: float64
Ridge: alpha=1000) | R^2: -0.0078 | RMSE: 0.011125
Top Ridge coeffs:
 S&P_vol_x_trend_dist        -0.000967
DJIA_vol_x_trend_dist       -0.000879
DJIA_vol_x_vlm_surprise      0.000814
NASDAQ_vol_x_vlm_surprise   -0.000748
NASDAQ_ewma_var             -0.000443
S&P_vol_speed_1w             0.000414
S&P_quarticity_3m           -0.000411
NASDAQ_ret                   0.000405
S&P_vol_x_vlm_surprise      -0.000362
NASDAQ_vol_speed_1w         -0.000326
dtype: float64
Lasso (alpha=1000) | R^2: -0.0041 | RMSE: 0.011105
Top Lasso c

C:\Users\rjsyo\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\linear_model\_coordinate_descent.py:681: ConvergenceWarning:

Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.353e-04, tolerance: 2.922e-05



OLS                | R^2: -1.4105 | RMSE: 0.022464
Top OLS coeffs:
 DJIA_ewma_vol           0.040534
S&P_ewma_vol           -0.038715
DJIA_quarticity_3m      0.031046
NASDAQ_quarticity_3m   -0.026587
S&P_vol_x_trend_dist   -0.025854
S&P_absrv_1m            0.018998
DJIA_ewma_var          -0.015991
DJIA_absrv_1m          -0.014531
S&P_absrv_3m            0.013855
DJIA_absrv_3m          -0.012458
dtype: float64
Ridge: alpha=1000) | R^2: -0.0035 | RMSE: 0.014495
Top Ridge coeffs:
 DJIA_vol_x_trend_dist       -0.000908
S&P_vol_x_trend_dist        -0.000885
DJIA_ret                    -0.000765
DJIA_vol_x_vlm_surprise      0.000699
NASDAQ_vol_x_vlm_surprise   -0.000582
S&P_quarticity_3m           -0.000453
S&P_price_trend_dist        -0.000446
NASDAQ_Volume               -0.000418
S&P_ret                     -0.000416
NASDAQ_ewma_var             -0.000352
dtype: float64
Lasso (alpha=0.0003039) | R^2: -0.0013 | RMSE: 0.014478
Top Lasso coeffs:
 DJIA_ret                -0.001384
DJIA_vol_x_tr

In [190]:
pca = PCA(n_components=.95).fit(train_scaled) # keep 95% of variance and fit to training set
train_pca = pca.transform(train_scaled)
test_pca = pca.transform(test_scaled)

# PCA
for target in targets:
    print(f"\n=== Target: {target} ===")
    y_train = train_scaled[target].copy()
    y_test  = test_scaled[target].copy()

    # 1) OLS on PCA components
    ols_pca = LinearRegression()
    ols_pca.fit(train_pca, y_train)
    yhat_pca = ols_pca.predict(test_pca)
    eval_and_report(y_test, yhat_pca, "OLS+PCA")

    results_sigma[target].update({
        "pca_model": ols_pca,
        "train_data_pca": pd.Series(ols_pca.predict(train_pca), index=y_train.index, name=f"PCA_train"),
        "yhat_pca": pd.Series(yhat_pca, index=y_test.index, name=f"{target}_PCA_pred")
    })


=== Target: S&P_next_ret ===
OLS+PCA            | R^2: -0.0074 | RMSE: 0.011123

=== Target: NASDAQ_next_ret ===
OLS+PCA            | R^2: -0.0053 | RMSE: 0.014507

=== Target: DJIA_next_ret ===
OLS+PCA            | R^2: -0.0341 | RMSE: 0.009627


In [191]:
# Pairs: (pretty name, next-return target key)
pairs = [
    ("S&P 500", "S&P_next_ret"),
    ("NASDAQ",  "NASDAQ_next_ret"),
    ("DJIA",    "DJIA_next_ret"),
]

def get_pred(results_dict, target_key, kind):
    """
    kind: 'ols', 'ridge', or 'pca'
    Prefer unstandardized preds if present, otherwise fall back to raw.
    """
    unstd_key = f"yhat_{kind}_unstd"
    std_key   = f"yhat_{kind}"
    if target_key in results_dict:
        if unstd_key in results_dict[target_key]:
            return results_dict[target_key][unstd_key]
        elif std_key in results_dict[target_key]:
            return results_dict[target_key][std_key]
    return None

fig = make_subplots(
    rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.06,
    subplot_titles=[p[0] for p in pairs]
)

for i, (label, next_col) in enumerate(pairs, start=1):
    if next_col not in testing_data.columns:
        continue

    # True = next-period return from testing_data (unscaled)
    y_true = testing_data[next_col].dropna().sort_index().rename("True")

    # Predictions for the same target
    yhat_ols   = get_pred(results_sigma, next_col, "ols")
    yhat_ridge = get_pred(results_sigma, next_col, "ridge")
    yhat_pca   = get_pred(results_sigma, next_col, "pca")
    yhat_lasso   = get_pred(results_sigma, next_col, "lasso")

    parts = [y_true]
    if yhat_ols is not None:
        parts.append(yhat_ols.rename("OLS").reindex(y_true.index))
    if yhat_ridge is not None:
        parts.append(yhat_ridge.rename("Ridge").reindex(y_true.index))
    if yhat_pca is not None:
        parts.append(yhat_pca.rename("PCA").reindex(y_true.index))
    if yhat_lasso is not None:
        parts.append(yhat_lasso.rename("Lasso").reindex(y_true.index))

    df = pd.concat(parts, axis=1).dropna(how="any")
    if df.empty:
        continue

    show_leg = (i == 1)

    # True next_ret
    fig.add_trace(
        go.Scatter(x=df.index, y=df["True"], name="True next_ret",
                   mode="lines", line=dict(width=1.6),
                   showlegend=show_leg, legendgroup="true"),
        row=i, col=1
    )
    """
    # OLS prediction
    if "OLS" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["OLS"], name="OLS prediction",
                       mode="lines", line=dict(width=1.4, dash="dash"),
                       showlegend=show_leg, legendgroup="ols"),
            row=i, col=1
        )
    """
    # Ridge prediction
    if "Ridge" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["Ridge"], name="Ridge prediction",
                       mode="lines", line=dict(width=1.4, dash="dot"),
                       showlegend=show_leg, legendgroup="ridge"),
            row=i, col=1
        )
    # PCA prediction 
    if "PCA" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["PCA"], name="PCA prediction",
                       mode="lines", line=dict(width=1.4, dash="longdash"),
                       showlegend=show_leg, legendgroup="pca"),
            row=i, col=1
        )
    # Lasso prediction  
    if "Lasso" in df:
        fig.add_trace(
            go.Scatter(x=df.index, y=df["Lasso"], name="Lasso prediction",
                       mode="lines", line=dict(width=1.4, dash="dash"),
                       showlegend=show_leg, legendgroup="lasso"),
            row=i, col=1
        )

fig.update_layout(
    title="Testing: True Next-Period Log Returns vs OLS, Ridge & PCA Predictions",
    height=900,
    hovermode="x unified",
    template="plotly_white",
    margin=dict(t=80, r=30, b=80, l=70),
    legend=dict(orientation="h", yanchor="top", y=-0.12, xanchor="left", x=0)
)

for r in range(1, 4):
    fig.update_yaxes(title_text="Log return", row=r, col=1)

# Range tools on the bottom axis
fig.update_xaxes(
    rangeselector=dict(buttons=[
        dict(step="all", label="All"),
        dict(count=3, step="year", stepmode="backward", label="3Y"),
        dict(count=1, step="year", stepmode="backward", label="1Y"),
        dict(count=6, step="month", stepmode="backward", label="6M"),
        dict(count=1, step="month", stepmode="backward", label="1M"),
    ]),
    rangeslider=dict(visible=True),
    row=3, col=1
)

fig.show()


Combine the drift and diffusion

In [198]:
combined = pd.DataFrame(data['S&P_Close']).join([data['NASDAQ_Close'], data['DJIA_Close']])
models = ['ridge','lasso','pca']

for model in models:
    for target in targets:
        df = pd.DataFrame(pd.concat([results_sigma[target][f'train_data_{model}'],results_sigma[target][f'yhat_{model}']])).join(pd.Series(pd.concat([results[target][f'train_data_{model}'],results[target][f'yhat_{model}']]),name='mu'))
        df['mu'] = df['mu'] - (data[target].mean())
        df['total'] = df[0] + df['mu']
        combined[f'{target}_pred_{model}'] = df['total']
combined = combined.dropna()


In [195]:
combined['S&P_next_ret_pred_lasso'].sum()

np.float64(-0.08793843451645794)

In [199]:
# --- config ---
is_log_returns = True
dash_map = {"ridge": "dot", "pca": "dash", "lasso": "longdash"}

pairs = [
    ("S&P 500",  "S&P_next_ret",  "S&P_Close"),
    ("NASDAQ",   "NASDAQ_next_ret","NASDAQ_Close"),
    ("DJIA",     "DJIA_next_ret", "DJIA_Close"),
]

fig = make_subplots(
    rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.06,
    subplot_titles=[p[0] for p in pairs]
)

for i, (label, target_key, close_col) in enumerate(pairs, start=1):
    if close_col not in combined.columns:
        continue

    close = combined[close_col].dropna()
    if close.empty:
        continue

    # Actual Close
    show_leg = (i == 1)
    fig.add_trace(
        go.Scatter(
            x=close.index, y=close.values,
            name=f"{label} — Actual", mode="lines",
            line=dict(width=1.7),
            showlegend=show_leg, legendgroup=f"{label}_actual"
        ),
        row=i, col=1
    )

    # For each model, overlay estimated close path
    for m in models:
        pred_col = f"{target_key}_pred_{m}"
        if pred_col not in combined.columns:
            continue

        rhat = combined[pred_col].dropna()
        idx = close.index.intersection(rhat.index)
        if idx.empty:
            continue

        s = close.loc[idx]
        r = rhat.loc[idx]

        base = float(s.iloc[0])
        if is_log_returns:
            # r_t moves price t-1 -> t, shift to anchor at first date
            cum = r.shift(1).fillna(0.0).cumsum()
            est = base * np.exp(cum)
        else:
            growth = (1.0 + r).shift(1).fillna(1.0).cumprod()
            est = base * growth

        fig.add_trace(
            go.Scatter(
                x=idx, y=est.values,
                name=f"{label} — {m.upper()} (anchored)",
                mode="lines",
                line=dict(width=1.3, dash=dash_map.get(m, "dash")),
                showlegend=show_leg, legendgroup=f"{label}_{m}"
            ),
            row=i, col=1
        )

fig.update_layout(
    title="Actual vs Estimated Close (Anchored) — Ridge & PCA",
    height=900,
    hovermode="x unified",
    template="plotly_white",
    margin=dict(t=80, r=30, b=80, l=70),
    legend=dict(orientation="h", yanchor="top", y=-0.12, xanchor="left", x=0)
)

for r in range(1, 4):
    fig.update_yaxes(title_text="Price", row=r, col=1)

fig.update_xaxes(
    rangeselector=dict(buttons=[
        dict(step="all", label="All"),
        dict(count=3, step="year", stepmode="backward", label="3Y"),
        dict(count=1, step="year", stepmode="backward", label="1Y"),
        dict(count=6, step="month", stepmode="backward", label="6M"),
        dict(count=1, step="month", stepmode="backward", label="1M"),
    ]),
    rangeslider=dict(visible=True),
    row=3, col=1
)

fig.show()


Pretty interesting results here... I think we need to move to backtesting to implement entry and exit strategies and compare against a baseline. Afterwards, we can try to implement some more advanced models as well as refine features.